In [2]:
import json
import random
import pickle
import os
import glob
import numpy as np
import redis
import pandas as pd
from multiprocessing import Pool
from tqdm.notebook import tqdm
from collections import defaultdict
from transformers import AutoTokenizer

In [2]:
redisd = redis.Redis(host='localhost', port=6379, decode_responses=True)

In [100]:
# Loading 3hop data
dir_path = "../data/doc_paths"
print("Loading training data...")
with open(os.path.join(dir_path, "train_data_3hop.json")) as f:
    train_data = [json.loads(line) for line in f.readlines()]
print("Loading dev data...")
with open(os.path.join(dir_path, "dev_data_3hop.json")) as f:
    dev_data = [json.loads(line) for line in f.readlines()]
print("Loading test data...")
with open(os.path.join(dir_path, "test_data_3hop.json")) as f:
    test_data = [json.loads(line) for line in f.readlines()]
print("Loading dev open data...")
with open(os.path.join(dir_path, "dev_open_data_3hop.json")) as f:
    dev_open_data = [json.loads(line) for line in f.readlines()]
print("Loading test open data...")
with open(os.path.join(dir_path, "test_open_data_3hop.json")) as f:
    test_open_data = [json.loads(line) for line in f.readlines()]
data = train_data + dev_data + test_data + dev_open_data + test_open_data

Loading training data...
Loading dev data...
Loading test data...
Loading dev open data...
Loading test open data...


In [ ]:
# Loading 4hop data
dir_path = "../data/doc_paths"
print("Loading training data...")
with open(os.path.join(dir_path, "train_data_4hop.json")) as f:
    train_data = [json.loads(line) for line in f.readlines()]
print("Loading dev data...")
with open(os.path.join(dir_path, "dev_data_4hop.json")) as f:
    dev_data = [json.loads(line) for line in f.readlines()]
print("Loading test data...")
with open(os.path.join(dir_path, "test_data_4hop.json")) as f:
    test_data = [json.loads(line) for line in f.readlines()]
print("Loading dev open data...")
with open(os.path.join(dir_path, "dev_open_data_4hop.json")) as f:
    dev_open_data = [json.loads(line) for line in f.readlines()]
print("Loading test open data...")
with open(os.path.join(dir_path, "test_open_data_4hop.json")) as f:
    test_open_data = [json.loads(line) for line in f.readlines()]
data = train_data + dev_data + test_data + dev_open_data + test_open_data
del train_data, dev_data, test_data, dev_open_data, test_open_data

Loading training data...
Loading dev data...
Loading test data...
Loading dev open data...


In [96]:
# Loading evi dev data to test the retrieval
with open("../data/rawdata/dev_evi.json") as f:
    evi_dev = json.load(f)
with open("../data/doc_paths/evi_data_4hop.json") as f:
    evi_data = [json.loads(line) for line in f.readlines()][-len(evi_dev):]
data = evi_data

# BM25

In [4]:
import re
import pandas as pd
import pickle
from rank_bm25 import *
from nltk.tokenize import word_tokenize
from nltk.stem import PorterStemmer
from gensim.parsing.preprocessing import STOPWORDS

In [9]:
passages = pd.read_csv("../data/codred_passages.tsv", sep="\t")

In [25]:
docs = passages['text'].tolist()

In [32]:
def tokenize(sentence):
    sentence = sentence.lower()
    text = re.sub("[^a-zA-z0-9 ]", "", sentence)
    text = word_tokenize(text)
    return [ps.stem(word) for word in text if not word in STOPWORDS]

In [33]:
def initializer():
    global ps
    ps = PorterStemmer()

In [34]:
tokenized_docs = []
pbar = tqdm(total=len(docs))
with Pool(48, initializer=initializer) as p:
    for doc in p.imap(tokenize, docs):
        tokenized_docs.append(doc)
        pbar.update(1)

  0%|          | 0/5193458 [00:00<?, ?it/s]

In [35]:
bm25 = BM25Okapi(tokenized_docs)

In [37]:
with open("../data/bm25_docs.pkl", "wb") as f:
    pickle.dump(bm25, f)

In [5]:
with open("../data/bm25_docs.pkl", "rb") as f:
    bm25 = pickle.load(f)

In [6]:
passages = pd.read_csv("../data/codred_passages.tsv", sep="\t")

In [7]:
with open("../data/title2id.json") as f:
    title2id = json.load(f)

In [8]:
lid2idx = {lid: i for i, lid in enumerate(passages["id"].tolist())}

In [9]:
question_template = {
    "naive": "what is the relation between {head} and {tail}?"
}

In [10]:
def process(sample, method="mean", topk=1):
    query = tokenize(question_template["naive"].format(head=sample["h_name"], tail=sample["t_name"]))
    
    paths = [path[1:] for path in sample['paths']]
    doc_paths = [[item[0] for item in path] for path in paths]
    cand_passages = [each for each in list(set(sum(doc_paths, [])))]
    
    cand_passages_indice = [lid2idx[title2id[each.split("_")[0]] + "_" + each.split("_")[1]] for each in cand_passages]
    scores = bm25.get_batch_scores(query, cand_passages_indice)
    score_dict = {passage: score for passage, score in zip(cand_passages, scores)}
    
    doc_path_score = []
    for path in doc_paths:
        passage_scores = []
        for passage in path:
            passage_scores.append(score_dict[passage])
        if method == "mean":
            doc_path_score.append(np.mean(passage_scores))
        elif method == "min":
            doc_path_score.append(np.min(passage_scores))
    ranked_paths = [doc_paths[idx] for idx in np.argsort(doc_path_score)[::-1][:topk]]
    return ranked_paths

In [11]:
def initializer(
        _question_template,
        _lid2idx,
        _bm25
    ):
    global question_template
    global lid2idx
    global bm25
    question_template = _question_template
    lid2idx = _lid2idx
    bm25 = _bm25

In [ ]:
ranked_paths = []
pbar = tqdm(total=len(data))
with Pool(4, initializer=initializer, initargs=(question_template, lid2idx, bm25)) as p:
    for res in p.imap(process, data):
        ranked_paths.append(res)
        pbar.update(1)

In [98]:
def get_cover_sent(title, pid):
    doc = json.loads(redisd.get(f'codred-doc-open-{title}'))
    cover_sentences = [f"{title}_{pid}_{i}" for i in range(len(doc['sentence_mapping'][pid]))]
    return cover_sentences

path_recall = []
sentence_recall = []
evis_num = []
topk = 1
for true, predict in zip(evi_dev, ranked_paths):
    evis = [f"{true['doc_h']}_{pid}_{sid}" for pid, sid in true['evis_h']
           ] + [f"{true['doc_t']}_{pid}_{sid}" for pid, sid in true['evis_t']]
    evis = set(evis)
    evis_num.append(len(evis))
    
    if topk == 1:
        pred = predict[0]
    elif topk == 5:
        pred = list(set(sum(predict[:5], [])))
    else:
        raise NotImplementedError()
    
    cover_sentences = []
    for p in pred:
        title, pid = p.split("_")
        pid = int(pid)
        cover_sentences += get_cover_sent(title, pid)
    cover_sentences = set(cover_sentences)
    
    if evis.issubset(cover_sentences):
        path_recall.append(1)
    else:
        path_recall.append(0)
    
    sentence_recall.append((len(evis.intersection(cover_sentences)), len(evis)))

In [99]:
path_recall_lq_3hop = [path_recall[i] for i in range(len(path_recall)) if evis_num[i] <= 3]
path_recall_ge_3hop = [path_recall[i] for i in range(len(path_recall)) if evis_num[i] > 3]

sentence_recall_lq_3hop = [sentence_recall[i] for i in range(len(sentence_recall)) if evis_num[i] <= 3]
sentence_recall_ge_3hop = [sentence_recall[i] for i in range(len(sentence_recall)) if evis_num[i] > 3]

print(sum(path_recall_lq_3hop)/len(path_recall_lq_3hop), sum(path_recall_ge_3hop)/len(path_recall_ge_3hop))
print(
    sum([each[0] for each in sentence_recall_lq_3hop])/sum([each[1] for each in sentence_recall_lq_3hop]),
    sum([each[0] for each in sentence_recall_ge_3hop])/sum([each[1] for each in sentence_recall_ge_3hop])
)
print(
    sum(path_recall)/len(path_recall),
    sum([each[0] for each in sentence_recall])/sum([each[1] for each in sentence_recall])
)

0.3626984126984127 0.16540008940545373
0.6199882075471698 0.522241034323534
0.23648841864455247 0.5424752837788356


BM25 3hop

- 0.3547619047619048 0.15556548949485918
- 0.6055424528301887 0.4949207326458365
- 0.22733771804403774 0.5178200903210057

BM25 4hop

- 0.3626984126984127 0.16540008940545373
- 0.6199882075471698 0.522241034323534
- 0.23648841864455247 0.5424752837788356

In [15]:
ranked_paths = []
pbar = tqdm(total=len(data))
with Pool(8, initializer=initializer, initargs=(question_template, lid2idx, bm25)) as p:
    for res in p.imap(process, data):
        ranked_paths.append(res)
        pbar.update(1)

  0%|          | 0/366775 [00:00<?, ?it/s]

OSError: [Errno 12] Cannot allocate memory

In [ ]:
result = {}
for i, sample in enumerate(data):
    h, t, doc_h, doc_t = sample["h"], sample["t"], sample["doch_title"], sample["doct_title"]

    key = f"{h}|{t}|{doc_h}|{doc_t}"
    output = [[], []]
    for passage in ranked_paths[i][0]:
        doc, index = passage.split("_")
        if doc == doc_h:
            output[0].append(int(index))
        if doc == doc_t:
            output[1].append(int(index))
    result[key] = output

In [116]:
with open("../data/retrieval_index/path_mining_3_hop_bm25_open_shared_entities.json", "w") as f:
    json.dump(result, f)

# Random retrieval baselines

## Scoring

In [6]:
def get_cover_sent(title, pid):
    doc = json.loads(redisd.get(f'codred-doc-open-{title}'))
    cover_sentences = [f"{title}_{pid}_{i}" for i in range(len(doc['sentence_mapping'][pid]))]
    return cover_sentences

In [7]:
path_recall = []
sentence_recall = []
evis_num = []
topk = 1
for true, predict in zip(evi_dev, evi_data):
    evis = [f"{true['doc_h']}_{pid}_{sid}" for pid, sid in true['evis_h']
           ] + [f"{true['doc_t']}_{pid}_{sid}" for pid, sid in true['evis_t']]
    evis = set(evis)
    evis_num.append(len(evis))
    
    predict = [[p[0] for p in each[1:]]for each in predict['paths']]
    random.shuffle(predict)
    if topk == 1:
        pred = predict[0]
    elif topk == 5:
        pred = list(set(sum(predict[:5], [])))
    else:
        raise NotImplementedError()
    
    cover_sentences = []
    for p in pred:
        title, pid = p.split("_")
        pid = int(pid)
        cover_sentences += get_cover_sent(title, pid)
    cover_sentences = set(cover_sentences)
    
    if evis.issubset(cover_sentences):
        path_recall.append(1)
    else:
        path_recall.append(0)
    
    sentence_recall.append((len(evis.intersection(cover_sentences)), len(evis)))

NameError: name 'evi_dev' is not defined

In [63]:
path_recall_lq_3hop = [path_recall[i] for i in range(len(path_recall)) if evis_num[i] <= 3]
path_recall_ge_3hop = [path_recall[i] for i in range(len(path_recall)) if evis_num[i] > 3]

sentence_recall_lq_3hop = [sentence_recall[i] for i in range(len(sentence_recall)) if evis_num[i] <= 3]
sentence_recall_ge_3hop = [sentence_recall[i] for i in range(len(sentence_recall)) if evis_num[i] > 3]

print(sum(path_recall_lq_3hop)/len(path_recall_lq_3hop), sum(path_recall_ge_3hop)/len(path_recall_ge_3hop))
print(
    sum([each[0] for each in sentence_recall_lq_3hop])/sum([each[1] for each in sentence_recall_lq_3hop]),
    sum([each[0] for each in sentence_recall_ge_3hop])/sum([each[1] for each in sentence_recall_ge_3hop])
)
print(
    sum(path_recall)/len(path_recall),
    sum([each[0] for each in sentence_recall])/sum([each[1] for each in sentence_recall])
)

0.2246031746031746 0.09342869915064819
0.5029481132075472 0.42958288440818837
0.14069202173291392 0.444769925546198


random 4hop:

- 0.20317460317460317 0.10326329906124274
- 0.49233490566037735 0.4362013236878559
- 0.1392622247640835 0.4478213108751373

random 3hop:

- 0.2246031746031746 0.09342869915064819
- 0.5029481132075472 0.42958288440818837
-0.14069202173291392 0.444769925546198

# Inference

In [10]:
result = {}
#ranked_paths = []
pbar = tqdm(total=len(data))
for i, sample in enumerate(data):
    h, t, doc_h, doc_t = sample["h"], sample["t"], sample["doch_title"], sample["doct_title"]
    
    paths = sample["paths"]
    random.shuffle(paths)

    paths = [each[0] for each in paths[0][1:]]
    #ranked_paths.append([paths])
    key = f"{h}|{t}|{doc_h}|{doc_t}"
    output = [[], []]
    for passage in paths:
        doc, index = passage.split("_")
        if doc == doc_h:
            output[0].append(int(index))
        if doc == doc_t:
            output[1].append(int(index))
    result[key] = output
    pbar.update(1)

  0%|          | 0/366775 [00:00<?, ?it/s]

In [9]:
len(data)

366775

In [11]:
with open("../data/retrieval_index/path_mining_4_hop_random_open_shared_entities.json", "w") as f:
    json.dump(result, f)

# Contextual DPR Inference

## Generate querys

In [5]:
question_template = {
    "naive": "what is the relation between {head} and {tail}?"
}

In [6]:
with open("../data/title2id.json") as f:
    title2id = json.load(f)

In [7]:
passages = pd.read_csv("../data/codred_passages.tsv", sep="\t")
passage_dict = {}
passages.set_index("id", inplace=True)
for idx, (text, title) in tqdm(passages.iterrows()):
    passage_dict[idx] = (title, text)

0it [00:00, ?it/s]

In [8]:
records = []
queries = []
queries_map = {}
max_path_num = -1
pbar = tqdm(total=len(data))
for i, sample in enumerate(data):
    all_paths = sample['paths']
    if max_path_num > 0 and len(all_paths) > max_path_num:
        all_paths = all_paths[:max_path_num]
    for j, path in enumerate(all_paths):
        doc_path = [pid for pid, ent in path[1:]]
        for k in range(len(doc_path)):
            if k == 0:
                query = question_template['naive'].format(head=sample['h_name'], tail=sample['t_name'])
            else:
                title, pid = doc_path[k-1].split("_")
                lid = f"{title2id[title]}_{pid}"
                passage = passage_dict[lid][1]
                query = question_template['naive'].format(head=sample['h_name'], tail=sample['t_name']) + " " + passage
            target_passage = doc_path[k]
            records.append((i, j, target_passage))
            queries.append(query)
    pbar.update(1)

  0%|          | 0/366775 [00:00<?, ?it/s]

In [9]:
outputs = []
output_list = []
output_mapping = {}
cur = 0
for idx, query in enumerate(queries):
    if query not in output_mapping:
        output_mapping[query] = cur
        cur += 1
        output = {
            "question": query,
            "answers": ['n/a'],
            "id": idx
        }
        outputs.append(output)
    output_list.append(output_mapping[query])

In [10]:
queries = list(zip(queries, output_list))

In [14]:
with open("../data/DPR/inference/codred_questions_record_all_3hop_dataset_contextual.jsonl", "w") as f:
    json.dump(records, f)
with open("../data/DPR/inference/codred_questions_query_all_3hop_dataset_contextual.jsonl", "w") as f:
    json.dump(queries, f)
with open("../data/DPR/inference/codred_questions_output_all_3hop_dataset_contextual.jsonl", "w") as f:
    json.dump(outputs, f)

# Load queries for inference

In [15]:
with open("../data/DPR/inference/codred_questions_record_all_3hop_dataset_contextual.jsonl") as f:
    records = json.load(f)
with open("../data/DPR/inference/codred_questions_query_all_3hop_dataset_contextual.jsonl") as f:
    queries = json.load(f)
with open("../data/DPR/inference/codred_questions_output_all_3hop_dataset_contextual.jsonl") as f:
    outputs = json.load(f)

In [8]:
pure_queries = []
last = -1
for (idx, query), record in zip(enumerate(queries), records):
    if query.endswith("?") and record[0] != last:
        pure_queries.append(idx)
        last = record[0]

In [9]:
# Loading auxillary data
with open("../data/title2id.json") as f:
    title2id = json.load(f)
with open("../data/id2title.json") as f:
    id2title = json.load(f)

In [9]:
!ls /nas/luka-group/DPR/outputs/2022-11-04/01-36-19/question_tensor.npy

/nas/luka-group/DPR/outputs/2022-11-04/01-36-19/question_tensor.npy


In [10]:
question_embedding = np.load("/nas/luka-group/DPR/outputs/2022-11-04/01-36-19/question_tensor.npy")

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 3497/3497 [00:14<00:00, 3359.73it/s]

In [11]:
pure_question_embedding = question_embedding[pure_queries]

In [14]:
finetune_path = "/nas/luka-group/DPR/outputs/codred_finetune_ext"
def load_passages(path):
    passage_data_dir = path
    passage_pattern = "codred_passages*"
    passage_files = glob.glob(os.path.join(passage_data_dir, passage_pattern))

    passage_arrays = defaultdict(list)
    for file_path in passage_files:
        with open(file_path, "rb") as f:
            data = pickle.load(f)
            pbar = tqdm(total=len(data))
            for idx, embedding in data:
                doc_id, passage_id = idx.split(":")[1].split("_")
                title = id2title[doc_id]
                passage_arrays[title].append((int(passage_id), embedding))
                pbar.update(1)
    for key, value in tqdm(passage_arrays.items()):
        sorted_array = sorted(value, key=lambda x: x[0])
        passage_arrays[key] = np.array([each[1] for each in sorted_array])
    return passage_arrays
passage_arrays = load_passages(finetune_path)


 99%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▍ | 1284830/1298365 [00:01<00:00, 868122.99it/s]

100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1298365/1298365 [00:10<00:00, 125338.48it/s]


  6%|█████████▏                                                                                                                                                 | 77027/1298363 [00:00<00:01, 770059.60it/s]

 12%|██████████████████▋                                                                                                                                       | 157704/1298363 [00:00<00:01, 791648.64it/s]

 19%|████████████████████████████▌                                                                                                                             | 240624/129836

100%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 257881/257881 [00:09<00:00, 27198.35it/s]


100%|█████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 1298365/1298365 [00:12<00:00, 105964.13it/s]


In [12]:
def get_rank_scores(sample, query_array, passage_arrays, topk=5, method="mean"):
    
    paths = [path[1:] for path in sample['paths']]
    doc_paths = [[item[0] for item in path] for path in paths]
    cand_passages = [each.split("_") for each in list(set(sum(doc_paths, [])))]
    try:
        cand_arrays = np.array([passage_arrays[title][int(idx)]for title, idx in cand_passages])
    except ValueError:
        print(sample['paths'])
    
    scores = np.matmul(query_array, cand_arrays.T)
    score_dict = {"_".join(cand_passage): s for cand_passage, s in zip(cand_passages, scores)}

    doc_path_score = []
    for path in doc_paths:
        passage_scores = []
        for passage in path:
            passage_scores.append(score_dict[passage])
        doc_path_score.append(passage_scores)
    return doc_path_score

In [15]:
ranked_scores = []
k=1;method="mean"
for i, sample in enumerate(evi_data):
    ranked_scores.append(get_rank_scores(
                sample, pure_question_embedding[i], passage_arrays, topk=k, method=method))

In [16]:
len(records), len(question_embedding)

(364787, 364787)

In [17]:
cand_passages = []
for _, _, target in records:
    title, idx = target.split("_")
    cand_passages.append(passage_arrays[title][int(idx)])
cand_passages = np.array(cand_passages)

In [18]:
scores = np.sum(question_embedding * cand_passages, axis=1)

In [41]:
all_scores = defaultdict(list)
for (i, j, _), s in zip(records, scores):
    all_scores[(i,j)].append(s)

In [42]:
for i, sample_scores in enumerate(ranked_scores):
    for j, path_scores in enumerate(sample_scores):
        seq_scores = all_scores[(i, j)]
        n = len(seq_scores)
        for k in range(1, n):
            all_scores[(i, j)] = (seq_scores[k] + path_scores[k-1]) / 2

In [43]:
agg_scores = defaultdict(list)
for i, j in all_scores:
    agg_scores[i].append((j, np.exp(np.mean(np.log(all_scores[(i, j)])))))
    #agg_scores[i].append((j, np.mean(all_scores[(i, j)])))

In [44]:
for key in agg_scores:
    agg_scores[key] = sorted(agg_scores[key], key=lambda x: -x[1])[:5]

In [45]:
ranked_paths = []
for i in agg_scores:
    j = agg_scores[i][0][0]
    ranked_paths.append([[each[0] for each in data[i]['paths'][j][1:]]])

In [46]:
def get_cover_sent(title, pid):
    doc = json.loads(redisd.get(f'codred-doc-open-{title}'))
    cover_sentences = [f"{title}_{pid}_{i}" for i in range(len(doc['sentence_mapping'][pid]))]
    return cover_sentences

path_recall = []
sentence_recall = []
evis_num = []
topk = 1
for true, predict in zip(evi_dev, ranked_paths):
    evis = [f"{true['doc_h']}_{pid}_{sid}" for pid, sid in true['evis_h']
           ] + [f"{true['doc_t']}_{pid}_{sid}" for pid, sid in true['evis_t']]
    evis = set(evis)
    evis_num.append(len(evis))
    
    if topk == 1:
        pred = predict[0]
    elif topk == 5:
        pred = list(set(sum(predict[:5], [])))
    else:
        raise NotImplementedError()
    
    cover_sentences = []
    for p in pred:
        title, pid = p.split("_")
        pid = int(pid)
        cover_sentences += get_cover_sent(title, pid)
    cover_sentences = set(cover_sentences)
    
    if evis.issubset(cover_sentences):
        path_recall.append(1)
    else:
        path_recall.append(0)
    
    sentence_recall.append((len(evis.intersection(cover_sentences)), len(evis)))

In [47]:
path_recall_lq_3hop = [path_recall[i] for i in range(len(path_recall)) if evis_num[i] <= 3]
path_recall_ge_3hop = [path_recall[i] for i in range(len(path_recall)) if evis_num[i] > 3]

sentence_recall_lq_3hop = [sentence_recall[i] for i in range(len(sentence_recall)) if evis_num[i] <= 3]
sentence_recall_ge_3hop = [sentence_recall[i] for i in range(len(sentence_recall)) if evis_num[i] > 3]

print(sum(path_recall_lq_3hop)/len(path_recall_lq_3hop), sum(path_recall_ge_3hop)/len(path_recall_ge_3hop))
print(
    sum([each[0] for each in sentence_recall_lq_3hop])/sum([each[1] for each in sentence_recall_lq_3hop]),
    sum([each[0] for each in sentence_recall_ge_3hop])/sum([each[1] for each in sentence_recall_ge_3hop])
)
print(
    sum(path_recall)/len(path_recall),
    sum([each[0] for each in sentence_recall])/sum([each[1] for each in sentence_recall])
)

0.4023809523809524 0.17925793473401877
0.6444575471698113 0.5179313529321226
0.2596511295396054 0.5441230318564628


# Inference

In [11]:
with open("../data/DPR/inference/codred_questions_record_all_3hop_dataset_contextual.jsonl") as f:
    records = json.load(f)
with open("../data/DPR/inference/codred_questions_query_all_3hop_dataset_contextual.jsonl") as f:
    queries = json.load(f)

In [8]:
# Loading auxillary data
with open("../data/title2id.json") as f:
    title2id = json.load(f)
with open("../data/id2title.json") as f:
    id2title = json.load(f)

In [9]:
# Loading context embeddings
finetune_path = "/nas/luka-group/DPR/outputs/codred_finetune_ext"
def load_passages(path):
    passage_data_dir = path
    passage_pattern = "codred_passages*"
    passage_files = glob.glob(os.path.join(passage_data_dir, passage_pattern))

    passage_arrays = defaultdict(list)
    for file_path in passage_files:
        with open(file_path, "rb") as f:
            data = pickle.load(f)
            pbar = tqdm(total=len(data))
            for idx, embedding in data:
                doc_id, passage_id = idx.split(":")[1].split("_")
                title = id2title[doc_id]
                passage_arrays[title].append((int(passage_id), embedding))
                pbar.update(1)
    for key, value in tqdm(passage_arrays.items()):
        sorted_array = sorted(value, key=lambda x: x[0])
        passage_arrays[key] = np.array([each[1] for each in sorted_array])
    return passage_arrays
passage_arrays = load_passages(finetune_path)

  0%|          | 0/1298365 [00:00<?, ?it/s]

  0%|          | 0/1298363 [00:00<?, ?it/s]

  0%|          | 0/1298365 [00:00<?, ?it/s]

  0%|          | 0/1298365 [00:00<?, ?it/s]

  0%|          | 0/257881 [00:00<?, ?it/s]

In [10]:
# Loading question embedding
question_embedding = np.load("/nas/luka-group/DPR/outputs/question_3hop_ext/question_tensor_all.npy")

In [19]:
def get_rank_scores(sample, query_array, passage_arrays, topk=5, method="mean"):
    
    paths = [path[1:] for path in sample['paths']]
    doc_paths = [[item[0] for item in path] for path in paths]
    cand_passages = [each.split("_") for each in list(set(sum(doc_paths, [])))]
    try:
        cand_arrays = np.array([passage_arrays[title][int(idx)]for title, idx in cand_passages])
    except ValueError:
        print(sample['paths'])
    
    scores = np.matmul(query_array, cand_arrays.T)
    score_dict = {"_".join(cand_passage): s for cand_passage, s in zip(cand_passages, scores)}

    doc_path_score = []
    for path in doc_paths:
        passage_scores = []
        for passage in path:
            passage_scores.append(score_dict[passage])
        doc_path_score.append(passage_scores)
    return doc_path_score

In [12]:
cand_passages = []
for _, _, target in records:
    title, idx = target.split("_")
    cand_passages.append(passage_arrays[title][int(idx)])
cand_passages = np.array(cand_passages)

In [13]:
del passage_arrays

In [20]:
scores = []
for i, c_embedding in tqdm(enumerate(cand_passages)):
        scores.append(np.sum(question_embedding[queries[i][1]] * c_embedding))

0it [00:00, ?it/s]

In [23]:
all_scores = defaultdict(list)
for (i, j, _), s in zip(records, scores):
    all_scores[(i,j)].append(s)

In [24]:
del scores

In [25]:
agg_scores = defaultdict(list)
for i, j in all_scores:
    agg_scores[i].append((j, np.exp(np.mean(np.log(all_scores[(i, j)])))))

In [33]:
for key in agg_scores:
    agg_scores[key] = sorted(agg_scores[key], key=lambda x: -x[1])[:5]

In [35]:
ranked_paths = []
for i in agg_scores:
    j = agg_scores[i][0][0]
    ranked_paths.append([[each[0] for each in data[i]['paths'][j][1:]]])

In [41]:
pbar = tqdm(total=len(data))
result = {}
for i, sample in enumerate(data):
    h, t, doc_h, doc_t = sample["h"], sample["t"], sample["doch_title"], sample["doct_title"]

    paths = ranked_paths[i][0]
    key = f"{h}|{t}|{doc_h}|{doc_t}"
    output = [[], []]
    for passage in paths:
        doc, index = passage.split("_")
        if doc == doc_h:
            output[0].append(int(index))
        if doc == doc_t:
            output[1].append(int(index))
    result[key] = output
    pbar.update(1)

  0%|          | 0/366775 [00:00<?, ?it/s]

In [43]:
with open("../data/retrieval_index/path_mining_3_hop_finetune_ext_inference_open_shared_entities.json", "w") as f:
    json.dump(result, f)

# DPR Retrieval

# Scoring

In [4]:
# Loading evi dev data to test the retrieval
with open("../data/rawdata/dev_evi.json") as f:
    evi_dev = json.load(f)
with open("../data/doc_paths/evi_data_3hop.json") as f:
    evi_data = [json.loads(line) for line in f.readlines()][-len(evi_dev):]
data = evi_data

In [5]:
# Loading auxillary data
with open("../data/title2id.json") as f:
    title2id = json.load(f)
with open("../data/id2title.json") as f:
    id2title = json.load(f)

In [6]:
question_embedding = np.load("/nas/luka-group/DPR/outputs/question_tensor_dev_finetune.npy")

In [7]:
question_embedding.shape, len(data)

((3497, 768), 3497)

In [8]:
finetune_path = "/nas/luka-group/DPR/outputs/codred_finetune"
def load_passages(path):
    passage_data_dir = path
    passage_pattern = "codred_passages*"
    passage_files = glob.glob(os.path.join(passage_data_dir, passage_pattern))

    passage_arrays = defaultdict(list)
    for file_path in passage_files:
        with open(file_path, "rb") as f:
            data = pickle.load(f)
            pbar = tqdm(total=len(data))
            for idx, embedding in data:
                doc_id, passage_id = idx.split(":")[1].split("_")
                title = id2title[doc_id]
                passage_arrays[title].append((int(passage_id), embedding))
                pbar.update(1)
    for key, value in tqdm(passage_arrays.items()):
        sorted_array = sorted(value, key=lambda x: x[0])
        passage_arrays[key] = np.array([each[1] for each in sorted_array])
    return passage_arrays
passage_arrays_finetune = load_passages(finetune_path)

  0%|          | 0/1038692 [00:00<?, ?it/s]

  0%|          | 0/1038692 [00:00<?, ?it/s]

  0%|          | 0/1038690 [00:00<?, ?it/s]

  0%|          | 0/1038692 [00:00<?, ?it/s]

  0%|          | 0/1038692 [00:00<?, ?it/s]

  0%|          | 0/257881 [00:00<?, ?it/s]

In [15]:
def get_rank_passages(sample, query_array, passage_arrays, topk=5, method="mean"):
    
    paths = [path[1:] for path in sample['paths']]
    doc_paths = [[item[0] for item in path] for path in paths]
    cand_passages = [each.split("_") for each in list(set(sum(doc_paths, [])))]
    try:
        cand_arrays = np.array([passage_arrays[title][int(idx)]for title, idx in cand_passages])
    except ValueError:
        print(sample['paths'])
    
    scores = np.matmul(query_array, cand_arrays.T)
    score_dict = {"_".join(cand_passage): s for cand_passage, s in zip(cand_passages, scores)}

    doc_path_score = []
    for path in doc_paths:
        passage_scores = []
        for passage in path:
            passage_scores.append(score_dict[passage])
        if method == "mean":
            doc_path_score.append(np.mean(passage_scores))
        elif method == "min":
            doc_path_score.append(np.min(passage_scores))
    ranked_paths = [doc_paths[idx] for idx in np.argsort(doc_path_score)[::-1][:topk]]
    return ranked_paths

In [10]:
ranked_paths = []
k=1;method="mean"
for i, sample in enumerate(evi_data):
    ranked_paths.append(get_rank_passages(
                sample, question_embedding[i], passage_arrays, topk=k, method=method))

NameError: name 'passage_arrays' is not defined

In [ ]:
def get_cover_sent(title, pid):
    doc = json.loads(redisd.get(f'codred-doc-open-{title}'))
    cover_sentences = [f"{title}_{pid}_{i}" for i in range(len(doc['sentence_mapping'][pid]))]
    return cover_sentences

path_recall = []
sentence_recall = []
evis_num = []
topk = 1
for true, predict in zip(evi_dev, ranked_paths):
    evis = [f"{true['doc_h']}_{pid}_{sid}" for pid, sid in true['evis_h']
           ] + [f"{true['doc_t']}_{pid}_{sid}" for pid, sid in true['evis_t']]
    evis = set(evis)
    evis_num.append(len(evis))
    
    if topk == 1:
        pred = predict[0]
    elif topk == 5:
        pred = list(set(sum(predict[:5], [])))
    else:
        raise NotImplementedError()
    
    cover_sentences = []
    for p in pred:
        title, pid = p.split("_")
        pid = int(pid)
        cover_sentences += get_cover_sent(title, pid)
    cover_sentences = set(cover_sentences)
    
    if evis.issubset(cover_sentences):
        path_recall.append(1)
    else:
        path_recall.append(0)
    
    sentence_recall.append((len(evis.intersection(cover_sentences)), len(evis)))

In [ ]:
path_recall_lq_3hop = [path_recall[i] for i in range(len(path_recall)) if evis_num[i] <= 3]
path_recall_ge_3hop = [path_recall[i] for i in range(len(path_recall)) if evis_num[i] > 3]

sentence_recall_lq_3hop = [sentence_recall[i] for i in range(len(sentence_recall)) if evis_num[i] <= 3]
sentence_recall_ge_3hop = [sentence_recall[i] for i in range(len(sentence_recall)) if evis_num[i] > 3]

print(sum(path_recall_lq_3hop)/len(path_recall_lq_3hop), sum(path_recall_ge_3hop)/len(path_recall_ge_3hop))
print(
    sum([each[0] for each in sentence_recall_lq_3hop])/sum([each[1] for each in sentence_recall_lq_3hop]),
    sum([each[0] for each in sentence_recall_ge_3hop])/sum([each[1] for each in sentence_recall_ge_3hop])
)
print(
    sum(path_recall)/len(path_recall),
    sum([each[0] for each in sentence_recall])/sum([each[1] for each in sentence_recall])
)

DPR 3hop
- 0.373015873015873 0.16405900759946357
- 0.6235259433962265 0.5122364168077574
- 0.23934801258221333 0.5352740144025387

DPR 4hop
- 0.37857142857142856 0.17523468931604827
- 0.6426886792452831 0.5387101739264276
- 0.24849871318272806 0.5602343463932625

# Inference

In [4]:
# open setting dev
question_embedding = np.concatenate(
    [
        np.load("/nas/luka-group/DPR/outputs/question_finetune/question_tensor_train.npy"),
        np.load("/nas/luka-group/DPR/outputs/question_finetune/question_tensor_dev.npy"),
        np.load("/nas/luka-group/DPR/outputs/question_finetune/question_tensor_test.npy"),
        np.load("/nas/luka-group/DPR/outputs/question_finetune/question_tensor_dev_open.npy"),
        np.load("/nas/luka-group/DPR/outputs/question_finetune/question_tensor_test_open.npy"),
    ], axis=0)

In [5]:
# Loading auxillary data
with open("../data/title2id.json") as f:
    title2id = json.load(f)
with open("../data/id2title.json") as f:
    id2title = json.load(f)

In [6]:
finetune_path = "/nas/luka-group/DPR/outputs/codred_finetune"
def load_passages(path):
    passage_data_dir = path
    passage_pattern = "codred_passages*"
    passage_files = glob.glob(os.path.join(passage_data_dir, passage_pattern))

    passage_arrays = defaultdict(list)
    for file_path in passage_files:
        with open(file_path, "rb") as f:
            data = pickle.load(f)
            pbar = tqdm(total=len(data))
            for idx, embedding in data:
                doc_id, passage_id = idx.split(":")[1].split("_")
                title = id2title[doc_id]
                passage_arrays[title].append((int(passage_id), embedding))
                pbar.update(1)
    for key, value in tqdm(passage_arrays.items()):
        sorted_array = sorted(value, key=lambda x: x[0])
        passage_arrays[key] = np.array([each[1] for each in sorted_array])
    return passage_arrays
passage_arrays = load_passages(finetune_path)

  0%|          | 0/1038692 [00:00<?, ?it/s]

  0%|          | 0/1038692 [00:00<?, ?it/s]

  0%|          | 0/1038690 [00:00<?, ?it/s]

  0%|          | 0/1038692 [00:00<?, ?it/s]

  0%|          | 0/1038692 [00:00<?, ?it/s]

  0%|          | 0/257881 [00:00<?, ?it/s]

In [11]:
def get_rank_passages(sample, query_array, passage_arrays, topk=5, method="mean"):
    if len(sample['paths']) > 5000:
        paths = [path[1:] for path in sample['paths'][:5000]]
    else:
        paths = [path[1:] for path in sample['paths']]
    doc_paths = [[item[0] for item in path] for path in paths]
    cand_passages = [each.split("_") for each in list(set(sum(doc_paths, [])))]
    try:
        cand_arrays = np.array([passage_arrays[title][int(idx)]for title, idx in cand_passages])
    except ValueError:
        print(sample['paths'])
    
    scores = np.matmul(query_array, cand_arrays.T)
    score_dict = {"_".join(cand_passage): s for cand_passage, s in zip(cand_passages, scores)}

    doc_path_score = []
    for path in doc_paths:
        passage_scores = []
        for passage in path:
            passage_scores.append(score_dict[passage])
        if method == "mean":
            doc_path_score.append(np.mean(passage_scores))
        elif method == "min":
            doc_path_score.append(np.min(passage_scores))
    ranked_paths = [doc_paths[idx] for idx in np.argsort(doc_path_score)[::-1][:topk]]
    return ranked_paths

In [12]:
topk = 1
result = {}
passage_num = []
ranked_paths = []
pbar = tqdm(total=len(data))
for i, sample in enumerate(data):
    h, t, doc_h, doc_t = sample["h"], sample["t"], sample["doch_title"], sample["doct_title"]

    paths = get_rank_passages(data[i], question_embedding[i], passage_arrays, topk=topk, method="mean")
    if topk == 1:
        paths = paths[0]
        ranked_paths.append([paths])
    if topk == 5:
        paths = list(set(sum(paths, [])))
        passage_num.append(len(paths))
    key = f"{h}|{t}|{doc_h}|{doc_t}"
    output = [[], []]
    for passage in paths:
        doc, index = passage.split("_")
        if doc == doc_h:
            output[0].append(int(index))
        if doc == doc_t:
            output[1].append(int(index))
    result[key] = output
    pbar.update(1)

  0%|          | 0/366775 [00:00<?, ?it/s]

In [13]:
with open("../data/retrieval_index/path_mining_4_hop_finetune_inference_open_shared_entities.json", "w") as f:
    json.dump(result, f)

# Others

In [52]:
with open("../data/retrieval_index/path_mining_3_hop_dpr_finetune_inference.json") as f:
    exist_result = json.load(f)

In [53]:
for key in result:
    exist_result[key] = result[key]

In [54]:
with open("../data/retrieval_index/path_mining_3_hop_finetune_inference_open_shared_entities.json", "w") as f:
    json.dump(exist_result, f)

In [24]:
for method in ("min", "mean"):
    for k in (1, 5):
        print(method, k)
        ranked_paths = []
        for i, sample in enumerate(evi_data):
            ranked_paths.append(get_rank_passages(
                sample, question_embedding[i], passage_arrays, topk=k, method=method))
        print(eval_recall(ranked_paths, evi_data))

min 1
(0.1895910780669145, 0.28158183815452215)
min 5
(0.3668859022018873, 0.4051629439765654)
mean 1
(0.23934801258221333, 0.31154644208470644)
mean 5
(0.4212181870174435, 0.42646161357256196)


In [14]:
4Path:
min 1
(0.19016299685444668, 0.2895780051150895)
min 5
(0.3308550185873606, 0.401150895140665)
mean 1
(0.24792679439519588, 0.3273657289002558)
mean 5
(0.3966256791535602, 0.4248081841432225)

3Path:
min 1
(0.1895910780669145, 0.28158183815452215)
min 5
(0.3668859022018873, 0.4051629439765654)
mean 1
(0.23934801258221333, 0.31154644208470644)
mean 5
(0.4212181870174435, 0.42646161357256196)

SyntaxError: invalid syntax (3130782642.py, line 1)

# DPR extend ranking

In [41]:
def eval_recall(ranked_paths, data):
    path_recall = 0
    sentence_recall = 0
    sentence_total = 0
    token_level_precision = 0

    for idx, each in enumerate(data):
        h, t = each['key'].split("#")
    
        paths = ranked_paths[idx]
        
        cover_sentences = []
        doch = json.loads(redisd.get(f"codred-doc-{each['doc_h']}""))
        cover_sentences += [f"{each['doc_h']}_{passage_id}_{i}" for i in range(len(doch['sentence_mapping'][passage_id]))]
        doct = json.loads(redisd.get(f"codred-doc-{each['doc_t']}""))
        cover_sentences += [f"{each['doc_t']}_{passage_id}_{i}" for i in range(len(doct['sentence_mapping'][passage_id]))]
    
        predict = [
            f"{each['doc_h']}_{pid}_{sid}" for pid, sid in head_cover_sentences
        ] + [
            f"{each['doc_t']}_{pid}_{sid}" for pid, sid in tail_cover_sentences
        ]
        predict = set(predict)
    
        evis = [
            f"{each['doc_h']}_{pid}_{sid}" for pid, sid in each['evis_h']
        ] + [
            f"{each['doc_t']}_{pid}_{sid}" for pid, sid in each['evis_t']
        ]
        evis = set(evis)
    
        if evis.issubset(predict):
            path_recall += 1

        sentence_recall += len(evis.intersection(predict))
        sentence_total += len(evis)
    
        token_level_precision += get_token_level_precision(evis, predict)
    
    return sentence_recall/sentence_total, path_recall/len(data), token_level_precision/len(data)

SyntaxError: invalid syntax (2893688607.py, line 13)

In [40]:
def eval_recall(ranked_paths, data):
    all_recall = 0
    all_sent_recall = 0
    all_sent = 0
    for i in range(len(ranked_paths)):
        ranked_path = ranked_paths[i]
        if not ranked_path:
            continue
        sample = data[i]
        
        evis = []
        for each in sample['evis_h']:
            evis.append(f"{sample['doch_title']}_{each[0]}")
        for each in sample['evis_t']:
            evis.append(f"{sample['doct_title']}_{each[0]}")
    
        all_sent += len(evis)
        all_sent_recall += len(set(evis).intersection(set(sum(ranked_path, []))))
    
        recall = 0
        for path in ranked_path:
            if set(evis).issubset(set(path)):
                recall = 1
        all_recall += recall

    return all_recall/len(ranked_paths), all_sent_recall/all_sent

# MDR ranking score

In [3]:
data_tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")

In [5]:
def get_tokens(passage_handle):
    doc_title, passage_idx = passage_handle.split("_")
    passage_idx = int(passage_idx)
    doc = json.loads(redisd.get(f"codred-doc-{doc_title}"))
    doc_passage_idx = doc["passage_mapping"]
    passage_tokens = doc['tokens'][
            doc_passage_idx[passage_idx-1] if passage_idx >= 1 else 0:doc_passage_idx[passage_idx]]
    return passage_tokens

In [6]:
def move_cuda(inputs):
    for key in inputs:
        inputs[key] = inputs[key].cuda()
    return inputs

In [7]:
!cat ~/multihop_dense_retrieval/scripts/predict_all.py

import os
import sys
sys.path.append("../")
import argparse
import collections
from collections import defaultdict
import json
import logging
from os import path
import time

import faiss
import numpy as np
import torch
import torch.distributed as dist
from torch.utils.data import Dataset, DataLoader
from tqdm import tqdm
from transformers import AutoConfig, AutoTokenizer

import json
from mdr.retrieval.models.mhop_retriever import RobertaRetriever
from mdr.retrieval.utils.basic_tokenizer import SimpleTokenizer
from mdr.retrieval.utils.utils import (load_saved, move_to_cuda, para_has_answer)


class EvalDataset(Dataset):
	def __init__(self, args):
		self.ds_items = [json.loads(_) for _ in open(args.eval_input).readlines()]

	def __getitem__(self, idx):
		return idx, self.ds_items[idx]

	def __len__(self):
		return len(self.ds_items)

def collate_fn(batch):
	return batch[0]


def move_cuda(inputs):
	for key in inputs:
		inputs[key] = inputs[key].cuda()
	return inputs

def multi_hop_pred

In [8]:
import torch
from transformers import AutoConfig, AutoTokenizer
from mdr.retrieval.models.mhop_retriever import RobertaRetriever
from mdr.retrieval.utils.basic_tokenizer import SimpleTokenizer
from mdr.retrieval.utils.utils import (load_saved, move_to_cuda, para_has_answer)

In [9]:
class args:
    model_name = "roberta-base"
    model_path = "/nas/home/keminglu/multihop_dense_retrieval/logs/06-29-2022/test_run-seed16-bsz16-fp16False-lr2e-05-decay0.0-warm0.1-valbsz16-sharedTrue-multi1-schemenone/checkpoint_best.pt"
    indexpath = "/nas/luka-group/keming/MDR/finetune/embed.npy"
    id2doc_path = "/nas/luka-group/keming/MDR/finetune/id2doc.json"
    beam_size = 5
    topk = 5
    max_q_len = 512
    device = 0

In [10]:
bert_config = AutoConfig.from_pretrained(args.model_name)
tokenizer = AutoTokenizer.from_pretrained(args.model_name)
model = RobertaRetriever(bert_config, args)
model = load_saved(model, args.model_path, exact=False)
model = model.cuda()
model.eval()

RobertaRetriever(
  (encoder): RobertaModel(
    (embeddings): RobertaEmbeddings(
      (word_embeddings): Embedding(50265, 768, padding_idx=1)
      (position_embeddings): Embedding(514, 768, padding_idx=1)
      (token_type_embeddings): Embedding(1, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-05, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (encoder): BertEncoder(
      (layer): ModuleList(
        (0): BertLayer(
          (attention): BertAttention(
            (self): BertSelfAttention(
              (query): Linear(in_features=768, out_features=768, bias=True)
              (key): Linear(in_features=768, out_features=768, bias=True)
              (value): Linear(in_features=768, out_features=768, bias=True)
              (dropout): Dropout(p=0.1, inplace=False)
            )
            (output): BertSelfOutput(
              (dense): Linear(in_features=768, out_features=768, bias=True)
              (LayerNorm): LayerNorm((768,), eps=1e-

In [11]:
d = 768
xb = np.load(args.indexpath).astype('float32')
id2doc = json.load(open(args.id2doc_path))

In [12]:
doc2id = {item[0]: int(key) for key, item in id2doc.items()}

In [13]:
def get_ranked_path(
        sample,
        args,
        data_tokenizer,
        tokenizer,
        model,
        xb,
        doc2id,
        topk=5
    ):
    
    if not sample["paths"]:
        return []
    
    query = f"What is the relation between {sample['h_name']} and {sample['t_name']}"

    paths = [path[1:] for path in sample['paths']]
    doc_paths = [[item[0] for item in path] for path in paths]
    
    next_graph = defaultdict(set)
    for path in doc_paths:
        for i in range(len(path) - 1):
            if i == 0:
                next_graph["head"].add(path[i])
            next_graph[path[i]].add(path[i+1])

    inputs = []
    docs = []
    for key in next_graph:
        if key == "head":
            inputs.append(key)
            docs.append(query)
        else:
            inputs.append(key)
            docs.append(query + ". " + data_tokenizer.convert_tokens_to_string(get_tokens(key)))
    cand_passages = list(set(sum([list(each) for each in next_graph.values()], [])))
    
    
    with torch.no_grad():
        batch_q = docs
        bsize = len(batch_q)

        batch_q_encodes = tokenizer.batch_encode_plus(
            batch_q, max_length=args.max_q_len, pad_to_max_length=True, return_tensors="pt")
        batch_q_encodes = move_cuda(batch_q_encodes)
        q_embeds = model.encode_q(
            batch_q_encodes["input_ids"],
            batch_q_encodes["attention_mask"],
            batch_q_encodes.get("token_type_ids", None))
        q_embeds_numpy = q_embeds.cpu().contiguous().numpy()
    
    query_embed_dict = {query_passage: embedding for query_passage, embedding in zip(inputs, q_embeds_numpy)}
    cand_embed_dict = {cand_passage: xb[doc2id[cand_passage]] for cand_passage in cand_passages}
    
    path_scores = []
    for idx, path in enumerate(doc_paths):
        path_score = 0
        path_score += np.matmul(query_embed_dict["head"], cand_embed_dict[path[0]].T)
        for i in range(len(path) - 1):
            path_score += np.matmul(query_embed_dict[path[i]], cand_embed_dict[path[i+1]].T)
        path_score /= len(path)
        path_scores.append((idx, path_score))
    
    path_scores = sorted(path_scores, key=lambda x: x[1])
    output_paths = [doc_paths[idx] for idx, score in path_scores][:topk]
    return output_paths

In [68]:
sample['evis_h'], sample['evis_t'],sample['paths']

([[1, 0], [1, 2]],
 [[0, 2], [0, 3], [1, 0], [1, 2]],
 [[['Q6160770', None],
   ['Live Box_1', 'Q6160770'],
   ['Live Box_3', 'Q6083429'],
   ['Triumph of a Heart_1', 'Q42455']],
  [['Q6160770', None],
   ['Live Box_1', 'Q6160770'],
   ['Live Box_3', 'Q6083429'],
   ['Triumph of a Heart_3', 'Q42455']],
  [['Q6160770', None],
   ['Live Box_1', 'Q6160770'],
   ['Triumph of a Heart_6', 'Q42455'],
   ['Triumph of a Heart_1', 'Q3496129']],
  [['Q6160770', None],
   ['Live Box_1', 'Q6160770'],
   ['Triumph of a Heart_6', 'Q42455'],
   ['Triumph of a Heart_3', 'Q3033820']],
  [['Q6160770', None],
   ['Live Box_1', 'Q6160770'],
   ['Triumph of a Heart_2', 'Q42455'],
   ['Triumph of a Heart_1', 'Q3496129']],
  [['Q6160770', None],
   ['Live Box_1', 'Q6160770'],
   ['Triumph of a Heart_2', 'Q42455'],
   ['Triumph of a Heart_3', 'Q3033820']],
  [['Q6160770', None],
   ['Live Box_1', 'Q6160770'],
   ['Triumph of a Heart_4', 'Q42455'],
   ['Triumph of a Heart_1', 'Q3496129']],
  [['Q6160770', None]

In [23]:
topk = 5
result = {}
passage_num = []
pbar = tqdm(total=len(data))
for i, sample in enumerate(data):
    h, t, doc_h, doc_t = sample["h"], sample["t"], sample["doch_title"], sample["doct_title"]
    
    paths = get_ranked_path(sample, args, data_tokenizer, tokenizer,
                            model, xb, doc2id, topk=topk)
    if topk == 1:
        paths = paths[0]
    if topk == 5:
        paths = list(set(sum(paths, [])))
        passage_num.append(len(paths))
    key = f"{h}|{t}|{doc_h}|{doc_t}"
    output = [[], []]
    for passage in paths:
        doc, index = passage.split("_")
        if doc == doc_h:
            output[0].append(int(index))
        if doc == doc_t:
            output[1].append(int(index))
    result[key] = output
    pbar.update(1)


100%|██████████| 170288/170288 [4:49:27<00:00,  9.81it/s]

  0%|          | 557/170288 [00:57<5:12:13,  9.06it/s]


  1%|          | 1062/170288 [02:08<6:27:38,  7.28it/s]


  1%|          | 1632/170288 [03:05<5:27:36,  8.58it/s]


  1%|▏         | 2195/170288 [04:05<7:32:49,  6.19it/s]


  2%|▏         | 2722/170288 [05:10<12:35:53,  3.69it/s]


...

 98%|█████████▊| 167719/170288 [3:50:10<02:04, 20.64it/s]


 99%|█████████▉| 168456/170288 [3:50:56<01:57, 15.59it/s]


 99%|█████████▉| 169217/170288 [3:51:41<00:56, 19.07it/s]


100%|█████████▉| 169976/170288 [3:52:27<00:21, 14.33it/s]


100%|██████████| 170288/170288 [3:53:01<00:00, 11.22it/s]

In [25]:
max(passage_num), np.mean(passage_num)

(12, 3.812118293714178)

In [24]:
with open("../data/retrieval_index/path_mining_3_hop_mdr_top5_finetune_inference.json", "w") as f:
    json.dump(result, f)

In [26]:
for k in (1, 5):
    ranked_paths = []
    for i, sample in enumerate(data):
        ranked_paths.append(get_ranked_path(
                sample, args, data_tokenizer, tokenizer, model, xb, doc2id, topk=k))
    print(k, eval_recall(ranked_paths, data))

1 (0.114097798112668, 0.24099841327962895)
5 (0.26965970832141833, 0.37635786647137803)


In [18]:
k=5
ranked_paths = []
for i, sample in enumerate(evi_data):
    ranked_paths.append(get_ranked_path(
                sample, args, data_tokenizer, tokenizer, model, xb, doc2id, topk=k))

In [19]:
def get_cover_sent(title, pid):
    doc = json.loads(redisd.get(f'codred-doc-{title}'))
    cover_sentences = [f"{title}_{pid}_{i}" for i in range(len(doc['sentence_mapping'][pid]))]
    return cover_sentences

path_recall = []
sentence_recall = []
evis_num = []
topk = 5
for true, predict in zip(evi_dev, ranked_paths):
    evis = [f"{true['doc_h']}_{pid}_{sid}" for pid, sid in true['evis_h']
           ] + [f"{true['doc_t']}_{pid}_{sid}" for pid, sid in true['evis_t']]
    evis = set(evis)
    evis_num.append(len(evis))
    
    if topk == 1:
        pred = predict[0]
    elif topk == 5:
        pred = list(set(sum(predict[:5], [])))
    else:
        raise NotImplementedError()
    
    cover_sentences = []
    for p in pred:
        title, pid = p.split("_")
        pid = int(pid)
        cover_sentences += get_cover_sent(title, pid)
    cover_sentences = set(cover_sentences)
    
    if evis.issubset(cover_sentences):
        path_recall.append(1)
    else:
        path_recall.append(0)
    
    sentence_recall.append((len(evis.intersection(cover_sentences)), len(evis)))

In [20]:
path_recall_lq_3hop = [path_recall[i] for i in range(len(path_recall)) if evis_num[i] <= 3]
path_recall_ge_3hop = [path_recall[i] for i in range(len(path_recall)) if evis_num[i] > 3]

sentence_recall_lq_3hop = [sentence_recall[i] for i in range(len(sentence_recall)) if evis_num[i] <= 3]
sentence_recall_ge_3hop = [sentence_recall[i] for i in range(len(sentence_recall)) if evis_num[i] > 3]

print(sum(path_recall_lq_3hop)/len(path_recall_lq_3hop), sum(path_recall_ge_3hop)/len(path_recall_ge_3hop))
print(
    sum([each[0] for each in sentence_recall_lq_3hop])/sum([each[1] for each in sentence_recall_lq_3hop]),
    sum([each[0] for each in sentence_recall_ge_3hop])/sum([each[1] for each in sentence_recall_ge_3hop])
)
print(
    sum(path_recall)/len(path_recall),
    sum([each[0] for each in sentence_recall])/sum([each[1] for each in sentence_recall])
)

0.5174603174603175 0.29995529727313364
0.7435141509433962 0.6507618901031246
0.37832427795253076 0.6699621628219211
